# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find a location for a restaurant. This report will provide recommendation to the stakeholders interested in opening a **restaurant** in **Bangalore**, India.

As part of this analysis, I will try to find **locations with low density of restaurants** and which are **close to city**.

we will utilize data science to find few neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* distance of neighborhood from city

We have decided to use regularly spaced grid of locations, centered around city center, to define neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **geopy geocoder API**
* number of restaurants and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Bangalore city will be obtained using **geopy geocoder API** of well known location (Koramangala)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Berlin city center.

Let's first find the latitude & longitude of Bangalore city, using specific, well known address and geopy geocoder API.

In [26]:
#!pip install geopy
from geopy.geocoders import Nominatim

In [27]:
from geopy.geocoders import Nominatim
address = 'Koramangala, Bengaluru, India'
geolocator = Nominatim(user_agent="myGeocoder")
restaurant_location = geolocator.geocode(address)

print('Coordinate of {}: {} {}'.format(address, restaurant_location.latitude, restaurant_location.longitude))

Coordinate of Koramangala, Bengaluru, India: 12.9340114 77.6222304


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Koramangala. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [28]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Koramangala longitude={}, latitude={}'.format(restaurant_location.longitude, restaurant_location.latitude))
x, y = lonlat_to_xy(restaurant_location.longitude, restaurant_location.latitude)
print('Koramangala UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Koramangala longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Koramangala longitude=77.6222304, latitude=12.9340114
Koramangala UTM X=8897560.443142325, Y=2961111.479357545
Koramangala longitude=77.622230399947, latitude=12.934011400002687


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Now we will create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [30]:
restaurant_location_x, restaurant_location_y = lonlat_to_xy(restaurant_location.longitude, restaurant_location.latitude)

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = restaurant_location_x - 6000
x_step = 600
y_min = restaurant_location_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(restaurant_location_x, restaurant_location_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: Bangalore location and candidate neighborhood centers:

In [31]:
#!pip install folium

import folium

In [32]:
map_restaurant = folium.Map(location=[restaurant_location.latitude, restaurant_location.longitude], zoom_start=14)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude], popup='Koramangala').add_to(map_restaurant)
for lat, lon in zip(latitudes, longitudes):
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_restaurant)
map_restaurant

we have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Koramangala. 

Let's now use Geopy geaocoder API to get approximate addresses of those locations. We will also remove unnecessary information from address such as Bangalore South, Bangalore Urban, State, India etc since we have already defined our scope to find restaurant within this area.

In [33]:
print('Retrieving addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    lat_lon=str(lat)+','+str(lon)
    location = geolocator.reverse(lat_lon)
    address = location.address
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Bangalore South', '')
    address = address.replace(', Bangalore Urban', '')
    address = address.replace(', Karnataka,', '')
    address = address.replace(', India', '')
    addresses.append(address)
    print(' .', end='')
print(' done.')

Retrieving addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


Let's print first 10 addresses and examine if the addresses of the locations look right and in correct format.

In [34]:
addresses[:10]

['6th Cross Road, MICO Layout, BTM Layout Ward, South Zone, Bengaluru 560069',
 "Sri Devi Baker's, 10th Cross Road, BTM Layout 2nd Stage, BTM Layout Ward, South Zone, Bengaluru 560069",
 'IAS Officers Colony, BTM Layout Ward, South Zone, Bengaluru 76',
 'IAS Officers Colony, BTM Layout Ward, South Zone, Bengaluru 76',
 '29th Main Road, Mahadeshwara Nagara, BTM Layout Ward, South Zone, Bengaluru 76',
 'Madivala Lake, Kodichikkanahalli Road, Vakil Marina Layout, Bilekahalli, Bommanahalli Zone, Bengaluru 76',
 'Madivala Lake, Kodichikkanahalli Road, Vakil Marina Layout, Bilekahalli, Bommanahalli Zone, Bengaluru 76',
 '4th Main Road, Gurappana Palya, Jayanagar East Ward, South Zone, Bengaluru 560069',
 'BTM Layout 2nd Stage, BTM Layout Ward, South Zone, Bengaluru 560069',
 '8th Main Road, BTM Layout 2nd Stage, BTM Layout Ward, South Zone, Bengaluru 560069']

Addresses Look good. Let's now place all this into a Pandas dataframe.

In [35]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  6th Cross Road, MICO Layout, BTM Layout Ward, ...  12.913728  77.604103   
1  Sri Devi Baker's, 10th Cross Road, BTM Layout ...  12.912640  77.606624   
2  IAS Officers Colony, BTM Layout Ward, South Zo...  12.911553  77.609144   
3  IAS Officers Colony, BTM Layout Ward, South Zo...  12.910466  77.611664   
4  29th Main Road, Mahadeshwara Nagara, BTM Layou...  12.909379  77.614184   
5  Madivala Lake, Kodichikkanahalli Road, Vakil M...  12.908292  77.616704   
6  Madivala Lake, Kodichikkanahalli Road, Vakil M...  12.907206  77.619223   
7  4th Main Road, Gurappana Palya, Jayanagar East...  12.917500  77.601282   
8  BTM Layout 2nd Stage, BTM Layout Ward, South Z...  12.916413  77.603803   
9  8th Main Road, BTM Layout 2nd Stage, BTM Layou...  12.915325  77.606323   

              X             Y  Distance from center  
0  8.895760e+06  2.955396e+06           5992.495307  
1  8.896360e+06  2.955396e+06           5840.376700  
2  8.896960e+06  2.955396e+06           5747.173218  
3  8.897560e+06  2.955396e+06           5715.767665  
4  8.898160e+06  2.955396e+06           5747.173218  
5  8.898760e+06  2.955396e+06           5840.376700  
6  8.899360e+06  2.955396e+06           5992.495307  
7  8.894860e+06  2.955915e+06           5855.766389  
8  8.895460e+06  2.955915e+06           5604.462508  
9  8.896060e+06  2.955915e+06           5408.326913

...and let's now save/persist this data into local file.

In [36]:
df_locations.to_pickle('./locations.pkl')    
print("File Created!")

File Created!


### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category. We will include in out list only venues that have 'restaurant' in category name.

Foursquare credentials are defined in hidden cell bellow.

In [52]:
# The code was removed by Watson Studio for sharing.

In [38]:
# Category IDs were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):
import requests
food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

def is_restaurant(categories):
    restaurant_words = ['restaurant']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
    return restaurant

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Bangalore South', '')
    address = address.replace(', Bangalore Urban', '')
    address = address.replace(', Karnataka,', '')
    address = address.replace(', India', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results] 
        pass
        
    except:
        venues = []
    return venues

We will now search our neighborhood locations and get nearby restaurants in a dictionary.

In [42]:
import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []
    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res = is_restaurant(venue_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)

Obtaining venues around candidate locations:

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function

 .

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function

 .

...

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function

 .

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


 . . done.


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function

In [43]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 390
Average number of restaurants in neighborhood: 3.0247252747252746


In [44]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4e5274abc65ba127fb31f278', 'Udupi Gokul Cafe', 12.916289204505134, 77.6030389361417, 'Outer Ring Road (BTM 2nd Stage), Bangalore, Karnātaka', 316, 8895319.18259928, 2955823.26286001)
('501e33b7e4b0bd21efb024ba', 'Punjabi Sanjhaa Chullah', 12.916514667275667, 77.6053553926602, 'BTM Layout, Bangalore, Karnātaka', 348, 8895761.048410123, 2956072.2895127777)
('4dc02d645da386e218c1d71a', 'The Royal Tandoori', 12.913706150646641, 77.60651733313675, '7th Cross (BTM 2nd Stage), Bangalore, Karnātaka', 259, 8896243.960727287, 2955603.119047703)
('51f936ec498e78ca252cd806', 'The Barbeques', 12.91587392235698, 77.60595967782875, 'Behind BTM Water tank (BTM Layout, 2nd Stage), Bangalore, Karnātaka', 303, 8895938.878224023, 2955995.010680948)
('4fdc489fe4b049c33b3d8272', 'Emerald Restaurant', 12.915988151384797, 77.6059484873921, 'Behind BTM Water Tank, Bangalore 560076, Karnātaka', 300, 8895926.431158198, 2956017.2562883673)
('4d4976645129a35d0cff39

In [21]:
print('Restaurants around location')
print('---------------------------')
for i in range(1, 10):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 2: Flavours of China, Balaji's Veg, Momoz, The Royal Tandoori, Namaste, Golmaal Paratha
Restaurants around location 3: Flavours of China, Balaji's Veg, Momoz, Beijing Bites, Shaan-e-Punjab, Mast Kalandar, Golmaal Paratha, Swadishta Aahar
Restaurants around location 4: Mast Kalandar, Kacha Papad
Restaurants around location 5: Tongue Mridang, Kacha Papad, Biryani Bowl
Restaurants around location 6: 
Restaurants around location 7: gugabana
Restaurants around location 8: Udupi Gokul Cafe
Restaurants around location 9: Punjabi Sanjhaa Chullah, Udupi Gokul Cafe, Narmadha's Hyderabad Biriyani, Emerald Restaurant
Restaurants around location 10: Flavours of China, Balaji's Veg, Punjabi Sanjhaa Chullah, Narmadha's Hyderabad Biriyani, Daana Paani, The Royal Tandoori, Emerald Restaurant, The Barbeques


Let's now see all the restaurants in our area of interest (Koramangala) on map.

In [45]:
map_restaurant = folium.Map(location=[restaurant_location.latitude, restaurant_location.longitude], zoom_start=14)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude], popup='Koramangala').add_to(map_restaurant)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    color = 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_restaurant)
map_restaurant

Now we have all the restaurants in area within few kilometers from Koramangala. We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new restaurant!

## Methodology <a name="methodology"></a>

In this analysis, we will direct our efforts on detecting areas of Bangalore that have low restaurant density. We will limit our analysis to area ~6km around center.

In data gathering step we have collected the required **data: location of every restaurant within 6km from Bangalore center** (Koramangala).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Bangalore - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [46]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 3.0247252747252746


Address   Latitude  Longitude  \
0  6th Cross Road, MICO Layout, BTM Layout Ward, ...  12.913728  77.604103   
1  Sri Devi Baker's, 10th Cross Road, BTM Layout ...  12.912640  77.606624   
2  IAS Officers Colony, BTM Layout Ward, South Zo...  12.911553  77.609144   
3  IAS Officers Colony, BTM Layout Ward, South Zo...  12.910466  77.611664   
4  29th Main Road, Mahadeshwara Nagara, BTM Layou...  12.909379  77.614184   
5  Madivala Lake, Kodichikkanahalli Road, Vakil M...  12.908292  77.616704   
6  Madivala Lake, Kodichikkanahalli Road, Vakil M...  12.907206  77.619223   
7  4th Main Road, Gurappana Palya, Jayanagar East...  12.917500  77.601282   
8  BTM Layout 2nd Stage, BTM Layout Ward, South Z...  12.916413  77.603803   
9  8th Main Road, BTM Layout 2nd Stage, BTM Layou...  12.915325  77.606323   

              X             Y  Distance from center  Restaurants in area  
0  8.895760e+06  2.955396e+06           5992.495307                    1  
1  8.896360e+06  2.955396e+06           5840.376700                    6  
2  8.896960e+06  2.955396e+06           5747.173218                    8  
3  8.897560e+06  2.955396e+06           5715.767665                    2  
4  8.898160e+06  2.955396e+06           5747.173218                    3  
5  8.898760e+06  2.955396e+06           5840.376700                    0  
6  8.899360e+06  2.955396e+06           5992.495307                    1  
7  8.894860e+06  2.955915e+06           5855.766389                    1  
8  8.895460e+06  2.955915e+06           5604.462508                    4  
9  8.896060e+06  2.955915e+06           5408.326913                    9

In [47]:
restaurants.values()

dict_values([('4e5274abc65ba127fb31f278', 'Udupi Gokul Cafe', 12.916289204505134, 77.6030389361417, 'Outer Ring Road (BTM 2nd Stage), Bangalore, Karnātaka', 316, 8895319.18259928, 2955823.26286001), ('501e33b7e4b0bd21efb024ba', 'Punjabi Sanjhaa Chullah', 12.916514667275667, 77.6053553926602, 'BTM Layout, Bangalore, Karnātaka', 348, 8895761.048410123, 2956072.2895127777), ('4dc02d645da386e218c1d71a', 'The Royal Tandoori', 12.913706150646641, 77.60651733313675, '7th Cross (BTM 2nd Stage), Bangalore, Karnātaka', 259, 8896243.960727287, 2955603.119047703), ('51f936ec498e78ca252cd806', 'The Barbeques', 12.91587392235698, 77.60595967782875, 'Behind BTM Water tank (BTM Layout, 2nd Stage), Bangalore, Karnātaka', 303, 8895938.878224023, 2955995.010680948), ('4fdc489fe4b049c33b3d8272', 'Emerald Restaurant', 12.915988151384797, 77.6059484873921, 'Behind BTM Water Tank, Bangalore 560076, Karnātaka', 300, 8895926.431158198, 2956017.2562883673), ('4d4976645129a35d0cff39ac', 'punjabi dhaba', 12.91185

now let's calculate the **distance to nearest restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [48]:
distances_to_restaurants = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in restaurants.values():
        res_x = res[6]
        res_y = res[7]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_restaurants.append(min_distance)

df_locations['Distance to restaurants'] = distances_to_restaurants

In [27]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  6th Cross Road, MICO Layout, BTM Layout Ward, ...  12.913728  77.604103   
1  Sri Devi Baker's, 10th Cross Road, BTM Layout ...  12.912640  77.606624   
2  IAS Officers Colony, BTM Layout Ward, South Zo...  12.911553  77.609144   
3  IAS Officers Colony, BTM Layout Ward, South Zo...  12.910466  77.611664   
4  29th Main Road, Mahadeshwara Nagara, BTM Layou...  12.909379  77.614184   
5  Madivala Lake, Kodichikkanahalli Road, Vakil M...  12.908292  77.616704   
6  Madivala Lake, Kodichikkanahalli Road, Vakil M...  12.907206  77.619223   
7  4th Main Road, Gurappana Palya, Jayanagar East...  12.917500  77.601282   
8  BTM Layout 2nd Stage, BTM Layout Ward, South Z...  12.916413  77.603803   
9  8th Main Road, BTM Layout 2nd Stage, BTM Layou...  12.915325  77.606323   

              X             Y  Distance from center  Restaurants in area  \
0  8.895760e+06  2.955396e+06           5992.495307                    1   
1  8.896360e+06  2.955396e+06           5840.376700                    6   
2  8.896960e+06  2.955396e+06           5747.173218                    8   
3  8.897560e+06  2.955396e+06           5715.767665                    2   
4  8.898160e+06  2.955396e+06           5747.173218                    3   
5  8.898760e+06  2.955396e+06           5840.376700                    0   
6  8.899360e+06  2.955396e+06           5992.495307                    1   
7  8.894860e+06  2.955915e+06           5855.766389                    1   
8  8.895460e+06  2.955915e+06           5604.462508                    4   
9  8.896060e+06  2.955915e+06           5408.326913                    9   

   Distance to restaurants  
0               526.124573  
1               237.878044  
2               223.577744  
3               382.827769  
4                96.581417  
5               635.228301  
6               493.203597  
7               272.299559  
8               168.612974  
9               145.353117

In [49]:
print('Average distance to closest restaurant from each area center:', df_locations['Distance to restaurants'].mean())

Average distance to closest restaurant from each area center: 493.1273183864921


**on average restaurants can be found within ~500m** from every area center candidate.

Now we will create a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, we will show a few circles indicating distance of 1km, 2km and 3km from Koramangala.

In [51]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

In [31]:
from folium import plugins
from folium.plugins import HeatMap

map_restaurant = folium.Map(location=[restaurant_location.latitude, restaurant_location.longitude], zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_restaurant) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_restaurant)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude]).add_to(map_restaurant)
folium.Circle([restaurant_location.latitude, restaurant_location.longitude], radius=1000, fill=False, color='white').add_to(map_restaurant)
folium.Circle([restaurant_location.latitude, restaurant_location.longitude], radius=2000, fill=False, color='white').add_to(map_restaurant)
folium.Circle([restaurant_location.latitude, restaurant_location.longitude], radius=3000, fill=False, color='white').add_to(map_restaurant)
map_restaurant

Looks like a few pockets of low restaurant density closest to city center can be found **south, south-east and east from Koramangala**. 

Based on this we will now focus our analysis on areas *south-west, south, south-east and east from Bangalore center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**.

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of closest to Koramangala.

In [32]:
roi_x_min = restaurant_location_x - 2000
roi_y_max = restaurant_location_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_restaurant= folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_restaurant)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude]).add_to(map_restaurant)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_restaurant)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_restaurant)
map_restaurant

Above map shows all the pockets of low restaurant density in closest to Berlin center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [33]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


Now let's calculate  **number of restaurants in vicinity** (we'll use radius of **250 meters**) for each location candidate.

In [35]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[6]; res_y = res[7]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[6]; res_y = res[7]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_restaurant_distances = []

print('Retrieving data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, restaurants)
    roi_restaurant_distances.append(distance)
print('done.')


Retrieving data on location candidates... done.


Let's put this into dataframe

In [36]:
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to restaurant':roi_restaurant_distances
                                })

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0  12.916719  77.616723  8.898010e+06  2.957111e+06                   1   
1  12.916538  77.617143  8.898110e+06  2.957111e+06                   1   
2  12.918073  77.614574  8.897460e+06  2.957198e+06                   0   
3  12.917892  77.614994  8.897560e+06  2.957198e+06                   0   
4  12.917710  77.615414  8.897660e+06  2.957198e+06                   0   
5  12.917529  77.615834  8.897760e+06  2.957198e+06                   0   
6  12.917348  77.616254  8.897860e+06  2.957198e+06                   0   
7  12.917167  77.616674  8.897960e+06  2.957198e+06                   1   
8  12.916985  77.617093  8.898060e+06  2.957198e+06                   1   
9  12.916804  77.617513  8.898160e+06  2.957198e+06                   1   

   Distance to restaurant  
0              114.966556  
1              117.038991  
2              359.662992  
3              302.901380  
4              272.288494  
5              276.645626  
6              274.995012  
7              214.716262  
8              191.269155  
9              216.944016

Now we will **filter** these locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**.

In [37]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

df_good_locations = df_roi_locations[good_res_count]

Locations with no more than two restaurants nearby: 1928


Now we will show these locations on a map.

In [38]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_restaurant = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_restaurant)
HeatMap(restaurant_latlons).add_to(map_restaurant)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_restaurant)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude]).add_to(map_restaurant)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_restaurant) 
map_restaurant

We now have a bunch of locations close to Koramangala, and we know that each of those locations has no more than two restaurants in radius of 250m. These locations are potential candidates for a new restaurant

we will now show those locations in a form of heatmap

In [39]:
map_restaurant = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_restaurant)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude]).add_to(map_restaurant)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_restaurant)
map_restaurant

we will now **cluster** these locations to create **centers of zones containing good locations**. These zones, their centers and addresses will be the final result of our analysis. 

In [40]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_restaurant = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_restaurant)
HeatMap(restaurant_latlons).add_to(map_restaurant)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_restaurant)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude]).add_to(map_restaurant)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_restaurant) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_restaurant)
map_restaurant

Addresses of these cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see these zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [42]:
map_restaurant = folium.Map(location=roi_center, zoom_start=14)
folium.Marker([restaurant_location.latitude, restaurant_location.longitude]).add_to(map_restaurant)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_restaurant)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_restaurant)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_restaurant) 
map_restaurant

Finaly, we will **get the addresses of these candidate centers using reverse geocode** which can be presented to stakeholders.

In [45]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    lat_lon=str(lat)+','+str(lon)
    location = geolocator.reverse(lat_lon)
    addr = location.address
    addr = addr.replace(', Bangalore South', '')
    addr = addr.replace(', Bangalore Urban', '')
    addr = addr.replace(', Karnataka,', '')
    addr = addr.replace(', India', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, restaurant_location_x, restaurant_location_y)
    print('{}{} => {:.1f}km from Koramangala'.format(addr, ' '*(50-len(addr)), d/1000))  

Addresses of centers of areas recommended for further analysis

St Johns Medical College, Sarjapur Road, Jakkasandra, South Zone, Bengaluru 560034 => 1.4km from Koramangala
Madiwala Sarjapura Road, Jakkasandra, South Zone, Bengaluru - 560034 => 2.5km from Koramangala
2nd Cross, 4th C block, Maistripalaya, Koramangala, South Zone, Bengaluru 5560034 => 1.8km from Koramangala
Maruthi Nagara, Madivala, South Zone, Bengaluru - 560034 => 3.4km from Koramangala
Maistripalaya, Koramangala, South Zone, Bengaluru 560095 => 0.8km from Koramangala
Krupanidhi College, Sarjapur Road, Jakkasandra, South Zone, Bengaluru 5560034 => 3.1km from Koramangala
Jakkasandra, South Zone, Bengaluru - 560034        => 3.5km from Koramangala
St Johns Medical College, 4th Cross Road, Suddagunte Palya Ward, South Zone, Bengaluru - 560034 => 2.3km from Koramangala
Indian Institute of Astrophysics, Mahayogi Vemana Road, Koramangala 2nd Block, Koramangala, South Zone, Bengaluru - 560034 => 2.1km from Koramangala
St Joh

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants, all zones being close to Bangalore center (all less than 4km from Koramangala, and about half of those less than 2km from Koramangala). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations.

In [46]:
map_restaurant = folium.Map(location=roi_center, zoom_start=14)
folium.Circle([restaurant_location.latitude, restaurant_location.longitude], radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_restaurant)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_restaurant) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_restaurant)
map_restaurant

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Bangalore, there are pockets of low restaurant density close to city center. Highest concentration of restaurants was detected north and west from Koramangala, so we focused our attention to areas south, south-east and east. 

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-east from Koramangala) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues. This, of course, does not imply that those zones are actually optimal locations for a new restaurant. Purpose of this analysis was to only provide info on areas close to Bangalore center but not crowded with existing restaurants - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Bangalore areas close to center with low number of restaurants in order to aid stakeholders in narrowing down the search for optimal location for a new restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general areas that justify further analysis, and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.